In [1]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import numpy as np
import os
import librosa
from torch.utils import data
from sklearn.cluster import KMeans
import matplotlib.pyplot as plt
from sklearn.manifold import TSNE

import torch.utils.data
from torch import nn, optim
from torch.autograd import Variable
from torchvision import datasets, transforms
from torchvision.utils import save_image
from torch.utils.data import Dataset, DataLoader
from PIL import Image
import matplotlib.pyplot as plt
from scipy.misc import imresize

In [2]:
path = "/home/ddmnn3/PycharmProjects/ADOS/Data/clip_images/all/"
EPOCHS = 1000
BATCH_SIZE = 32
learning_rate = 1e-4
counter = 0
specs = list()
LOG_INTERVAL = 10
no_of_sample = 10


In [3]:
class ADOSClipImg(Dataset):

    def __init__(self, root_dir, im_name_list, resize_dim, transform=None):
        self.root_dir = root_dir
        self.im_list = im_name_list
        self.resize_dim = resize_dim
        self.transform = transform

    def __len__(self):
        return len(self.im_list)

    def __getitem__(self, idx):
        im = Image.open(os.path.join(self.root_dir, self.im_list[idx]))
        im = np.array(im)
        im = imresize(im, self.resize_dim, interp='nearest')
        im = im / 255

        if self.transform:
            im = self.transform(im)

        return im
    
class ToTensor(object):
    """Convert ndarrays in sample to Tensors. numpy image: H x W x C, torch image: C X H X W
    """

    def __call__(self, image, invert_arrays=True):

        if invert_arrays:
            image = image.transpose((2, 0, 1))

        return torch.from_numpy(image) 

In [4]:
class Conv_Block(nn.Module):
    def __init__(self, in_channels, out_channels, kernel_size, padding, stride, pool_kernel_size=(2, 2)):
        super(Conv_Block, self).__init__()
        self.conv1 = nn.Conv2d(in_channels, out_channels, kernel_size, padding, stride)
        self.conv2 = nn.Conv2d(out_channels, out_channels, kernel_size, padding, stride)
        self.pool = nn.MaxPool2d(pool_kernel_size)

    def forward(self, x):
        x = F.elu(self.conv1(x))
        x = F.elu(self.conv2(x))
        x = self.pool(x)

        return x

class VAE(nn.Module):
    def __init__(self):
        super(VAE, self).__init__()
        # Encoder
        self.block1 = Conv_Block(4, 64, (3, 3), 1, 1)  # 64
        self.block2 = Conv_Block(64, 128, (3, 3), 1, 1)  # 32
        self.block3 = Conv_Block(128, 256, (3, 3), 1, 1)  # 16
        self.block4 = Conv_Block(256, 32, (3, 3), 1, 1)  # 8

        # Decoder
        self.fct_decode = nn.Sequential(
            nn.Conv2d(16, 64, (3, 3), padding=1),
            nn.ELU(),
            nn.Upsample(scale_factor=2, mode='nearest'),  # 16
            nn.Conv2d(64, 64, (3, 3), padding=1),
            nn.ELU(),
            nn.Upsample(scale_factor=2, mode='nearest'),  # 32
            nn.Conv2d(64, 64, (3, 3), padding=1),
            nn.ELU(),
            nn.Upsample(scale_factor=2, mode='nearest'),  # 64
            nn.Conv2d(64, 16, (3, 3), padding=1),
            nn.ELU(),
            nn.Upsample(scale_factor=2, mode='nearest'),  # 128
        )

        self.final_decod_mean = nn.Conv2d(16, 4, (3, 3), padding=1)

    def encode(self, x):
        '''return mu_z and logvar_z'''

        x = F.elu(self.block1(x))
        x = F.elu(self.block2(x))
        x = F.elu(self.block3(x))
        x = F.elu(self.block4(x))

        return x[:, :16, :, :], x[:, 16:, :, :]  # output shape - batch_size x 16 x 8 x 8

    def reparameterize(self, mu: Variable, logvar: Variable) -> Variable:

        if self.training:
            # multiply log variance with 0.5, then in-place exponent
            # yielding the standard deviation

            sample_z = []
            for _ in range(no_of_sample):
                std = logvar.mul(0.5).exp_()  # type: Variable
                eps = Variable(std.data.new(std.size()).normal_())
                sample_z.append(eps.mul(std).add_(mu))

            return sample_z

        else:
            return mu

    def decode(self, z):

        z = self.fct_decode(z)
        z = self.final_decod_mean(z)
        z = F.sigmoid(z)

        return z.view(-1, 4 * 256 * 256)

    def forward(self, x):
        mu, logvar = self.encode(x)
        z = self.reparameterize(mu, logvar)
        if self.training:
            return [self.decode(z) for z in z], mu, logvar
        else:
            return self.decode(z), mu, logvar

    def loss_function(self, recon_x, x, mu, logvar) -> Variable:
        # how well do input x and output recon_x agree?

        if self.training:
            BCE = 0
            for recon_x_one in recon_x:
                BCE += F.binary_cross_entropy(recon_x_one, x.view(-1, 4 * 256 * 256))
            BCE /= len(recon_x)
        else:
            BCE = F.binary_cross_entropy(recon_x, x.view(-1, 4 * 256 * 256))

        KLD = -0.5 * torch.sum(1 + logvar - mu.pow(2) - logvar.exp())
        KLD /= BATCH_SIZE * 4 * 256 * 256

        return BCE + KLD

In [5]:
def train(epoch, model, optimizer, train_loader):
    # toggle model to train mode
    model.train()
    train_loss = 0
    # in the case of MNIST, len(train_loader.dataset) is 60000
    # each `data` is of BATCH_SIZE samples and has shape [128, 1, 28, 28]
    for batch_idx, data in enumerate(train_loader):
        data = Variable(data.type(torch.FloatTensor))
        data = data.cuda()
        optimizer.zero_grad()

        # push whole batch of data through VAE.forward() to get recon_loss
        recon_batch, mu, logvar = model(data)
        # calculate scalar loss
        loss = model.loss_function(recon_batch, data, mu, logvar)
        # calculate the gradient of the loss w.r.t. the graph leaves
        # i.e. input variables -- by the power of pytorch!
        loss.backward()
        #train_loss += loss.data[0]
        optimizer.step()
        if batch_idx % LOG_INTERVAL == 0:
            print('Train Epoch: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}'.format(epoch, batch_idx * len(data),
                                                                           len(train_loader.dataset),
                                                                           100. * batch_idx / len(train_loader),
                                                                           loss / len(data)))

    print('====> Epoch: {} Average loss: {:.4f}'.format(epoch, train_loss / len(train_loader.dataset)))

In [ ]:

image_files = []
for folder in os.listdir(path):
    image_files.append(os.listdir(path+folder+'/'))
image_files = [item for sublist in image_files for item in sublist]

In [ ]:
path

In [6]:
image_files = os.listdir(path)
train_dataset = ADOSClipImg(path, image_files, (256, 256), transforms.Compose([ToTensor()]))
train_loader = DataLoader(train_dataset, batch_size=BATCH_SIZE, num_workers=4, shuffle=True)

#Take only 1000 images in test
#test_dataset = CelebaDataset(root_dir, image_files[100000:101000], (128, 128), transforms.Compose([ToTensor()]))
#test_loader = DataLoader(test_dataset, batch_size=BATCH_SIZE, num_workers=10, shuffle=True)

In [7]:
model = VAE().cuda()

In [8]:
optimizer = optim.Adam(model.parameters(), lr=1e-4)

In [ ]:
for epoch in range(1, EPOCHS + 1):
    train(epoch, model, optimizer, train_loader)
    torch.save(model.state_dict(), "/home/ddmnn3/PycharmProjects/ADOS/Models/" + "model")

/home/ddmnn3/anaconda3/envs/spectre2/lib/python3.6/site-packages/ipykernel_launcher.py:15: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.3.0.
Use Pillow instead: ``numpy.array(Image.fromarray(arr).resize())``.
  from ipykernel import kernelapp as app
/home/ddmnn3/anaconda3/envs/spectre2/lib/python3.6/site-packages/ipykernel_launcher.py:15: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.3.0.
Use Pillow instead: ``numpy.array(Image.fromarray(arr).resize())``.
  from ipykernel import kernelapp as app
/home/ddmnn3/anaconda3/envs/spectre2/lib/python3.6/site-packages/ipykernel_launcher.py:15: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.3.0.
Use Pillow instead: ``numpy.array(Image.fromarray(arr).resize())``.
  from ipykernel import kernelapp as app
/home/ddmnn3/anaconda3/envs/spectre2/lib/python3.

Train Epoch: 1 [0/20131 (0%)]	Loss: 0.011311
Train Epoch: 1 [320/20131 (2%)]	Loss: 0.011433
Train Epoch: 1 [640/20131 (3%)]	Loss: 0.011382
Train Epoch: 1 [960/20131 (5%)]	Loss: 0.011371
Train Epoch: 1 [1280/20131 (6%)]	Loss: 0.011483
Train Epoch: 1 [1600/20131 (8%)]	Loss: 0.011378
Train Epoch: 1 [1920/20131 (10%)]	Loss: 0.011421
Train Epoch: 1 [2240/20131 (11%)]	Loss: 0.011279
Train Epoch: 1 [2560/20131 (13%)]	Loss: 0.011302
Train Epoch: 1 [2880/20131 (14%)]	Loss: 0.011348
Train Epoch: 1 [3200/20131 (16%)]	Loss: 0.011265
Train Epoch: 1 [3520/20131 (17%)]	Loss: 0.011306
Train Epoch: 1 [3840/20131 (19%)]	Loss: 0.011497
Train Epoch: 1 [4160/20131 (21%)]	Loss: 0.011427
Train Epoch: 1 [4480/20131 (22%)]	Loss: 0.011329
Train Epoch: 1 [4800/20131 (24%)]	Loss: 0.011333
Train Epoch: 1 [5120/20131 (25%)]	Loss: 0.011289
Train Epoch: 1 [5440/20131 (27%)]	Loss: 0.011409
Train Epoch: 1 [5760/20131 (29%)]	Loss: 0.011397
Train Epoch: 1 [6080/20131 (30%)]	Loss: 0.011389
Train Epoch: 1 [6400/20131 (32%)

/home/ddmnn3/anaconda3/envs/spectre2/lib/python3.6/site-packages/ipykernel_launcher.py:15: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.3.0.
Use Pillow instead: ``numpy.array(Image.fromarray(arr).resize())``.
  from ipykernel import kernelapp as app
/home/ddmnn3/anaconda3/envs/spectre2/lib/python3.6/site-packages/ipykernel_launcher.py:15: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.3.0.
Use Pillow instead: ``numpy.array(Image.fromarray(arr).resize())``.
  from ipykernel import kernelapp as app
/home/ddmnn3/anaconda3/envs/spectre2/lib/python3.6/site-packages/ipykernel_launcher.py:15: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.3.0.
Use Pillow instead: ``numpy.array(Image.fromarray(arr).resize())``.
  from ipykernel import kernelapp as app
/home/ddmnn3/anaconda3/envs/spectre2/lib/python3.

Train Epoch: 2 [0/20131 (0%)]	Loss: 0.011298
Train Epoch: 2 [320/20131 (2%)]	Loss: 0.011273
Train Epoch: 2 [640/20131 (3%)]	Loss: 0.011396
Train Epoch: 2 [960/20131 (5%)]	Loss: 0.011233
Train Epoch: 2 [1280/20131 (6%)]	Loss: 0.011217
Train Epoch: 2 [1600/20131 (8%)]	Loss: 0.011400
Train Epoch: 2 [1920/20131 (10%)]	Loss: 0.011385
Train Epoch: 2 [2240/20131 (11%)]	Loss: 0.011394
Train Epoch: 2 [2560/20131 (13%)]	Loss: 0.011231
Train Epoch: 2 [2880/20131 (14%)]	Loss: 0.011364
Train Epoch: 2 [3200/20131 (16%)]	Loss: 0.011275
Train Epoch: 2 [3520/20131 (17%)]	Loss: 0.011320
Train Epoch: 2 [3840/20131 (19%)]	Loss: 0.011305
Train Epoch: 2 [4160/20131 (21%)]	Loss: 0.011278
Train Epoch: 2 [4480/20131 (22%)]	Loss: 0.011353
Train Epoch: 2 [4800/20131 (24%)]	Loss: 0.011302
Train Epoch: 2 [5120/20131 (25%)]	Loss: 0.011295
Train Epoch: 2 [5440/20131 (27%)]	Loss: 0.011240
Train Epoch: 2 [5760/20131 (29%)]	Loss: 0.011258
Train Epoch: 2 [6080/20131 (30%)]	Loss: 0.011363
Train Epoch: 2 [6400/20131 (32%)

/home/ddmnn3/anaconda3/envs/spectre2/lib/python3.6/site-packages/ipykernel_launcher.py:15: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.3.0.
Use Pillow instead: ``numpy.array(Image.fromarray(arr).resize())``.
  from ipykernel import kernelapp as app
/home/ddmnn3/anaconda3/envs/spectre2/lib/python3.6/site-packages/ipykernel_launcher.py:15: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.3.0.
Use Pillow instead: ``numpy.array(Image.fromarray(arr).resize())``.
  from ipykernel import kernelapp as app
/home/ddmnn3/anaconda3/envs/spectre2/lib/python3.6/site-packages/ipykernel_launcher.py:15: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.3.0.
Use Pillow instead: ``numpy.array(Image.fromarray(arr).resize())``.
  from ipykernel import kernelapp as app
/home/ddmnn3/anaconda3/envs/spectre2/lib/python3.

...

Train Epoch: 745 [0/20131 (0%)]	Loss: 0.011100
Train Epoch: 745 [320/20131 (2%)]	Loss: 0.011139
Train Epoch: 745 [640/20131 (3%)]	Loss: 0.011126
Train Epoch: 745 [960/20131 (5%)]	Loss: 0.011122
Train Epoch: 745 [1280/20131 (6%)]	Loss: 0.011177
Train Epoch: 745 [1600/20131 (8%)]	Loss: 0.011007
Train Epoch: 745 [1920/20131 (10%)]	Loss: 0.011102
Train Epoch: 745 [2240/20131 (11%)]	Loss: 0.011216
Train Epoch: 745 [2560/20131 (13%)]	Loss: 0.011134
Train Epoch: 745 [2880/20131 (14%)]	Loss: 0.011157
Train Epoch: 745 [3200/20131 (16%)]	Loss: 0.011325
Train Epoch: 745 [3520/20131 (17%)]	Loss: 0.011026
Train Epoch: 745 [3840/20131 (19%)]	Loss: 0.011169
Train Epoch: 745 [4160/20131 (21%)]	Loss: 0.011133
Train Epoch: 745 [4480/20131 (22%)]	Loss: 0.011095
Train Epoch: 745 [4800/20131 (24%)]	Loss: 0.011115
Train Epoch: 745 [5120/20131 (25%)]	Loss: 0.011175
Train Epoch: 745 [5440/20131 (27%)]	Loss: 0.011215
Train Epoch: 745 [5760/20131 (29%)]	Loss: 0.011149
Train Epoch: 745 [6080/20131 (30%)]	Loss: 0

/home/ddmnn3/anaconda3/envs/spectre2/lib/python3.6/site-packages/ipykernel_launcher.py:15: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.3.0.
Use Pillow instead: ``numpy.array(Image.fromarray(arr).resize())``.
  from ipykernel import kernelapp as app
/home/ddmnn3/anaconda3/envs/spectre2/lib/python3.6/site-packages/ipykernel_launcher.py:15: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.3.0.
Use Pillow instead: ``numpy.array(Image.fromarray(arr).resize())``.
  from ipykernel import kernelapp as app
/home/ddmnn3/anaconda3/envs/spectre2/lib/python3.6/site-packages/ipykernel_launcher.py:15: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.3.0.
Use Pillow instead: ``numpy.array(Image.fromarray(arr).resize())``.
  from ipykernel import kernelapp as app
/home/ddmnn3/anaconda3/envs/spectre2/lib/python3.

Train Epoch: 746 [0/20131 (0%)]	Loss: 0.011099
Train Epoch: 746 [320/20131 (2%)]	Loss: 0.011146
Train Epoch: 746 [640/20131 (3%)]	Loss: 0.011135
Train Epoch: 746 [960/20131 (5%)]	Loss: 0.011007
Train Epoch: 746 [1280/20131 (6%)]	Loss: 0.011185
Train Epoch: 746 [1600/20131 (8%)]	Loss: 0.011229
Train Epoch: 746 [1920/20131 (10%)]	Loss: 0.011195
Train Epoch: 746 [2240/20131 (11%)]	Loss: 0.011248
Train Epoch: 746 [2560/20131 (13%)]	Loss: 0.011129
Train Epoch: 746 [2880/20131 (14%)]	Loss: 0.011112
Train Epoch: 746 [3200/20131 (16%)]	Loss: 0.011219
Train Epoch: 746 [3520/20131 (17%)]	Loss: 0.011155
Train Epoch: 746 [3840/20131 (19%)]	Loss: 0.011251
Train Epoch: 746 [4160/20131 (21%)]	Loss: 0.011136
Train Epoch: 746 [4480/20131 (22%)]	Loss: 0.011153
Train Epoch: 746 [4800/20131 (24%)]	Loss: 0.011106
Train Epoch: 746 [5120/20131 (25%)]	Loss: 0.011080
Train Epoch: 746 [5440/20131 (27%)]	Loss: 0.011006
Train Epoch: 746 [5760/20131 (29%)]	Loss: 0.011227
Train Epoch: 746 [6080/20131 (30%)]	Loss: 0

/home/ddmnn3/anaconda3/envs/spectre2/lib/python3.6/site-packages/ipykernel_launcher.py:15: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.3.0.
Use Pillow instead: ``numpy.array(Image.fromarray(arr).resize())``.
  from ipykernel import kernelapp as app
/home/ddmnn3/anaconda3/envs/spectre2/lib/python3.6/site-packages/ipykernel_launcher.py:15: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.3.0.
Use Pillow instead: ``numpy.array(Image.fromarray(arr).resize())``.
  from ipykernel import kernelapp as app
/home/ddmnn3/anaconda3/envs/spectre2/lib/python3.6/site-packages/ipykernel_launcher.py:15: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.3.0.
Use Pillow instead: ``numpy.array(Image.fromarray(arr).resize())``.
  from ipykernel import kernelapp as app
/home/ddmnn3/anaconda3/envs/spectre2/lib/python3.

Train Epoch: 747 [0/20131 (0%)]	Loss: 0.011172
Train Epoch: 747 [320/20131 (2%)]	Loss: 0.011205
Train Epoch: 747 [640/20131 (3%)]	Loss: 0.011086
Train Epoch: 747 [960/20131 (5%)]	Loss: 0.011213
Train Epoch: 747 [1280/20131 (6%)]	Loss: 0.011111
Train Epoch: 747 [1600/20131 (8%)]	Loss: 0.011147
Train Epoch: 747 [1920/20131 (10%)]	Loss: 0.011145
Train Epoch: 747 [2240/20131 (11%)]	Loss: 0.011160
Train Epoch: 747 [2560/20131 (13%)]	Loss: 0.011156
Train Epoch: 747 [2880/20131 (14%)]	Loss: 0.011170
Train Epoch: 747 [3200/20131 (16%)]	Loss: 0.011008
Train Epoch: 747 [3520/20131 (17%)]	Loss: 0.011149
Train Epoch: 747 [3840/20131 (19%)]	Loss: 0.011237
Train Epoch: 747 [4160/20131 (21%)]	Loss: 0.011035
Train Epoch: 747 [4480/20131 (22%)]	Loss: 0.011141
Train Epoch: 747 [4800/20131 (24%)]	Loss: 0.011089
Train Epoch: 747 [5120/20131 (25%)]	Loss: 0.011107
Train Epoch: 747 [5440/20131 (27%)]	Loss: 0.011207
Train Epoch: 747 [5760/20131 (29%)]	Loss: 0.011162
Train Epoch: 747 [6080/20131 (30%)]	Loss: 0

In [ ]:
def lossfn(x, target, mean, logvar):
    bce = nn.BCELoss()
    bce_loss = bce(x, target)

    scaling_factor = out.shape[0] * out.shape[1] * out.shape[2] * out.shape[3]

    kl_loss = -.5 * torch.sum(1 + logvar - mean ** 2 - torch.exp(logvar))
    kl_loss /= scaling_factor

    return bce_loss + kl_loss

In [ ]:
model.train()
train_loss = 0

In [ ]:
data.shape

In [ ]:


for epoch in range(2):
    print("Epoch #" + str(epoch))
    
    for batch_idx, data in enumerate(train_loader):
        data = Variable(data.type(torch.FloatTensor))
        data = data.cuda()
        optimizer.zero_grad()
        out, mean, logvar, _ = model(data)
        loss = lossfn(out, data, mean, logvar)
        loss.backward()
        optimizer.step()
        if batch_idx % LOG_INTERVAL == 0:
            print('Train Epoch: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}'.format(epoch, batch_idx * len(data),
                                                                           len(train_loader.dataset),
                                                                           100. * batch_idx / len(train_loader),
                                                                           loss.data[0] / len(data)))
            torch.save(model.state_dict(), "/home/ddmnn3/PycharmProjects/ADOS/Models/" + "model1")
            
        optimizer.zero_grad()
        torch.cuda.empty_cache()

In [ ]:
for epoch in range(1, EPOCHS + 1):
        train(epoch, model, optimizer, train_loader)
        #test(epoch, model, test_loader)

        

In [ ]:
# 64 sets of random ZDIMS-float vectors, i.e. 64 locations / MNIST
# digits in latent space
sample = Variable(torch.randn(64, 16, 8, 8))
if CUDA:
    sample = sample.cuda()
sample = model.decode(sample).cpu()

# save out as an 8x8 matrix of MNIST digits
# this will give you a visual idea of how well latent space can generate things
# that look like digits
save_image(sample.data.view(64, 3, 128, 128), './celeba/reconstruction' + str(epoch) + '.png')